In [ ]:
#what i need to do is to 

# 1. make gmaps query “company name san francisco” --> 
# 2. let a agent run over this and have him extract all the addresses where he actually thinks this could be the address of an actual office
# 3. create the interactive map for san francisco where each pin represents a company - the pin is the company profile pic and on click of it all the other metadata is displayed

In [16]:
#load all the offices which are located in san francisco and which are still active today
import json

def load_and_filter_companies(file_path):
    active_sf_companies = []

    with open(file_path, 'r') as json_file:
        for line in json_file:
            company = json.loads(line)
            if company.get('status') == "Active" and company.get('location') == "San Francisco":
                active_sf_companies.append(company)

    return active_sf_companies

# Path to your dataset
file_path = 'company_data.json'

# Load and filter the dataset
filtered_companies = load_and_filter_companies(file_path)

# Print or save the filtered results
for company in filtered_companies:
    print(json.dumps(company, indent=4))

# Optionally, save the filtered results to a new JSON file
with open('active_sf_companies.json', 'w') as json_file:
    for company in filtered_companies:
        json_file.write(json.dumps(company) + '\n')


{
    "url": "https://www.ycombinator.com/companies/jet-admin",
    "name": "Jet Admin",
    "status": "Active",
    "profile_picture_url": "https://bookface-images.s3.amazonaws.com/small_logos/36f3d929390edbb2302940824ff50512f48f5516.png",
    "tags": [
        "Y Combinator LogoW20",
        "developer-tools",
        "saas",
        "b2b",
        "San Francisco"
    ],
    "description": "Jet Admin - an app builder designed specifically for creating internal tools, admin panels, external portals, inventory apps, and other business applications really fast and without coding. \r\n\r\nIn Jet Admin, you can assemble multi-page apps with complex user flows, connected to multiple data sources. Setting up custom layouts, adding custom actions and workflows, binding and transforming dynamic values, using conditional rules and validations - all is done through a drag & drop and point & click visual builder.\r\n\r\nWe\u2019ve also added a variety of developer tools, so whenever necessary, y

In [32]:
#create all queries for the google maps text search
import json
import os
import asyncio
import aiohttp
from dotenv import load_dotenv
import nest_asyncio

# Apply the nest_asyncio patch
nest_asyncio.apply()

load_dotenv()

# Retrieve API key from environment variables
API_KEY = os.getenv('GOOGLE_MAPS_API_KEY')

BASE_URL = "https://places.googleapis.com/v1/places:searchText"

async def search_places(session, query, retries=3):
    print("query:", query)
    print("session:", session)

    headers = {
        'Content-Type': 'application/json',
        'X-Goog-Api-Key': API_KEY,
        'X-Goog-FieldMask': 'places.displayName,places.formattedAddress,places.types,places.websiteUri,places.rating,places.userRatingCount'
    }
    body = {
        "textQuery": query,
        "pageSize": 20  # Set to maximum number of results
    }
    for attempt in range(retries):
        try:
            async with session.post(BASE_URL, headers=headers, json=body) as response:
                if response.status == 200:
                    data = await response.json()
                    if 'places' in data:
                        return {"query": query, "results": data['places']}
                    else:
                        print(f"No results found in response for query: {query}")
                        print("Response data:", data)
                        return {"query": query, "results": []}
                elif response.status == 429:  # Too Many Requests
                    print(f"Error: {response.status}. Retrying in {2 ** attempt} seconds...")
                    await asyncio.sleep(2 ** attempt)
                else:
                    response.raise_for_status()
        except aiohttp.ClientError as e:
            print(f"Request failed: {e}. Retrying in {2 ** attempt} seconds...")
            await asyncio.sleep(2 ** attempt)
    return {"query": query, "results": []}

# Load the filtered companies from the JSON file
def load_filtered_companies(file_path):
    with open(file_path, 'r') as json_file:
        return [json.loads(line) for line in json_file]

# Create a list of queries with the company name + "San Francisco"
def create_queries(companies):
    return [f"{company['name']} San Francisco" for company in companies]

# Path to the filtered dataset
file_path = 'active_sf_companies.json'

# Load the filtered companies
filtered_companies = load_filtered_companies(file_path)

# Create the list of queries
queries = create_queries(filtered_companies)    

In [39]:
import aiohttp
import asyncio

async def search_places(query, retries=3):
    url = BASE_URL
    headers = {
        'Content-Type': 'application/json',
        'X-Goog-Api-Key': API_KEY,
        'X-Goog-FieldMask': 'places.displayName,places.formattedAddress,places.types,places.websiteUri,places.rating,places.userRatingCount'
    }
    body = {
        "textQuery": query,
        "pageSize": 20  # Set to maximum number of results
    }
    for attempt in range(retries):
        try:
            async with aiohttp.ClientSession() as session:
                async with session.post(url, headers=headers, json=body) as response:
                    if response.status == 200:
                        data = await response.json()
                        if 'places' in data:
                            # Print the response to verify the structure
                            #print(f"Response for query '{query}':", data['places'])
                            return {"query": query, "results": data['places']}
                        else:
                            #print(f"No results found in response for query: {query}")
                            #print("Response data:", data)
                            return {"query": query, "results": []}
                    elif response.status == 429:  # Too Many Requests
                        print(f"Error: {response.status}. Retrying in {2 ** attempt} seconds...")
                        await asyncio.sleep(2 ** attempt)
                    else:
                        response.raise_for_status()
        except aiohttp.ClientError as e:
            print(f"Request failed: {e}. Retrying in {2 ** attempt} seconds...")
            await asyncio.sleep(2 ** attempt)
    return {"query": query, "results": []}

# Example usage
for query in queries:
    response = await search_places(query)
    print("repsonse:", response)
    await asyncio.sleep(0.5)  # Wait for 500 milliseconds
    with open('search_results.json', 'a') as json_file:
        json.dump(response, json_file, indent=4)


repsonse: {'query': 'Jet Admin San Francisco', 'results': [{'types': ['point_of_interest', 'establishment'], 'formattedAddress': 'Alemany Blvd, San Francisco, CA 94112, USA', 'websiteUri': 'https://www.jetadmin.io/', 'displayName': {'text': 'JetAdmin', 'languageCode': 'en'}}]}
repsonse: {'query': 'Legionfarm San Francisco', 'results': [{'types': ['point_of_interest', 'establishment'], 'formattedAddress': '401 Van Ness Ave #101, San Francisco, CA 94102, USA', 'rating': 3, 'websiteUri': 'https://alwmcsf.org/', 'userRatingCount': 1, 'displayName': {'text': 'American Legion War Memorial Commission', 'languageCode': 'en'}}]}
repsonse: {'query': 'Menten AI San Francisco', 'results': [{'types': ['point_of_interest', 'establishment'], 'formattedAddress': '3154 17th St, San Francisco, CA 94110, USA', 'rating': 5, 'websiteUri': 'https://www.mindsdb.com/', 'userRatingCount': 2, 'displayName': {'text': 'MindsDB SF AI Collective', 'languageCode': 'en'}}]}
repsonse: {'query': 'Equator Therapeutics S

In [41]:
#fixing previously wrong formatted json file
import json

# Read the existing file
with open('search_results.json', 'r') as file:
    content = file.read()

# Fix the JSON format
content = content.replace('}{', '},{')
fixed_content = f'[{content}]'

# Write the fixed content to a new file
with open('fixed_search_results.json', 'w') as file:
    file.write(fixed_content)

# Verify the fixed JSON
with open('fixed_search_results.json', 'r') as file:
    data = json.load(file)
    print(json.dumps(data, indent=4))

[
    {
        "query": "Jet Admin San Francisco",
        "results": [
            {
                "types": [
                    "point_of_interest",
                    "establishment"
                ],
                "formattedAddress": "Alemany Blvd, San Francisco, CA 94112, USA",
                "websiteUri": "https://www.jetadmin.io/",
                "displayName": {
                    "text": "JetAdmin",
                    "languageCode": "en"
                }
            }
        ]
    },
    {
        "query": "Legionfarm San Francisco",
        "results": [
            {
                "types": [
                    "point_of_interest",
                    "establishment"
                ],
                "formattedAddress": "401 Van Ness Ave #101, San Francisco, CA 94102, USA",
                "rating": 3,
                "websiteUri": "https://alwmcsf.org/",
                "userRatingCount": 1,
                "displayName": {
                    "text": "Amer

In [61]:
import json
from openai import OpenAI
import os
from dotenv import load_dotenv

# Load environment variables from .env file
load_dotenv()

# Load the fixed JSON data
with open('fixed_search_results.json', 'r') as json_file:
    data = json.load(json_file)

def llm(entry):
    prompt = f"""
    You are given the result of the Google Maps Text Search API in JSON format. Your job is to find the address of the company. For example, if the query is "Jet Admin San Francisco" then you try to find, based on the API results, which address is the correct one. Sometimes the API response is empty, or the addresses from the API request do not contain the actual address where a company has its office. In the case there is no or no fitting address, please just return "No address found." Otherwise, return a JSON object containing the original query and the address. Only if its clear that this address is the correct one return it. Here is the API response:

    {entry}
    """
    messages = [
        {
            "role": "system",
            "content": prompt
        }
    ]
    client = OpenAI(
        api_key=os.environ.get("OPENAI_API_KEY"),
    )
    chat_completion = client.chat.completions.create(
        messages=messages,
        model="gpt-4",
        temperature=0.0
    )
    return chat_completion.choices[0].message.content

# Iterate over each entry and call the llm method
with open('new_fixed_processed_results.json', 'a') as json_file:
    for entry in data:
        result = llm(entry)
        print("result:", result)
        json.dump({
            "entry": entry,
            "result": result
        }, json_file, indent=4)
        json_file.write('\n')  # Ensure each entry is on a new line

print("Results saved to processed_results.json")

result: Based on the API response, the address of the company "Jet Admin" in San Francisco is 'Alemany Blvd, San Francisco, CA 94112, USA'. Here is the JSON object:

{
  "query": "Jet Admin San Francisco",
  "address": "Alemany Blvd, San Francisco, CA 94112, USA"
}
result: The API response does not contain the address for "Legionfarm San Francisco". The address provided is for the "American Legion War Memorial Commission", not Legionfarm. Therefore, the response is "No address found."
result: Based on the API response, it seems that the address for "Menten AI San Francisco" is not directly available. The address provided is for "MindsDB SF AI Collective" which may not be the same as Menten AI. Therefore, the correct response would be "No address found."
result: The API response does not contain the address for "Equator Therapeutics San Francisco". The addresses provided are for "Equator Coffees", which is not the same as the queried company. Therefore, the response is "No address found

In [64]:
#fix processed results to json format
import json
import os

# Function to read the existing content and fix the JSON format
def fix_json_format(file_path):
    with open(file_path, 'r') as file:
        content = file.read()
    
    # Fix the JSON format by ensuring it is a valid JSON array
    content = content.replace('}\n{', '},{')
    fixed_content = f'[{content}]'
    
    # Write the fixed content to a new file
    with open('fixed_processed_results.json', 'w') as file:
        file.write(fixed_content)

    # Verify the fixed JSON
    with open('fixed_processed_results.json', 'r') as file:
        data = json.load(file)
        print(json.dumps(data, indent=4))

# Fix the JSON format of the existing file
fix_json_format('processed_results.json')

[
    {
        "entry": {
            "query": "Jet Admin San Francisco",
            "results": [
                {
                    "types": [
                        "point_of_interest",
                        "establishment"
                    ],
                    "formattedAddress": "Alemany Blvd, San Francisco, CA 94112, USA",
                    "websiteUri": "https://www.jetadmin.io/",
                    "displayName": {
                        "text": "JetAdmin",
                        "languageCode": "en"
                    }
                }
            ]
        },
        "result": "Based on the API response, the address of the company \"Jet Admin\" in San Francisco is 'Alemany Blvd, San Francisco, CA 94112, USA'. Here is the JSON object:\n\n{\n  \"query\": \"Jet Admin San Francisco\",\n  \"address\": \"Alemany Blvd, San Francisco, CA 94112, USA\"\n}"
    },
    {
        "entry": {
            "query": "Legionfarm San Francisco",
            "results": [
     

In [76]:
#iter over processed results and extract for each query the address / addresses and add it to an dataset and in the case there is no address found, just add an empty string

#what i need to do now is to put the result in a json format like {address:some_adress} 
import json
from openai import OpenAI
import os
from dotenv import load_dotenv

# Load environment variables from .env file
load_dotenv()

with open('fixed_processed_results.json', 'r') as json_file:
    data = json.load(json_file)

def llm(entry):
    prompt = f"""
    You are given the results of a query. The query either contains no address, one address, or multiple addresses. Your task is to return a JSON object containing the address(es). For example:

    example_json = {{
        "addresses": [
            "Alemany Blvd, San Francisco, CA 94112, USA"
        ]
    }}

    Make sure your JSON response only includes the "address" key. If there is no address provide and empty list []. Here is the entry:

    {entry}
    """
    messages = [
        {
            "role": "user",
            "content": prompt
        }
    ]
    client = OpenAI(
        api_key=os.environ.get("OPENAI_API_KEY"),
    )
    chat_completion = client.chat.completions.create(
        messages=messages,
        model="gpt-4o",
        temperature=0.0,
        response_format={ "type": "json_object" }
    )
    return chat_completion.choices[0].message.content

# Iterate over each entry and call the llm method
with open('new_fixed_processed_results.json', 'a') as json_file:
    for entry in data:
        query = entry["entry"]["query"]
        result = llm(entry.get("result", "No result found"))
        print("result:", result)
        try:
            result_json = json.loads(result)  # Parse the JSON response
            combined_result = {
                "query": query,
                "result": result_json
            }
            json.dump(combined_result, json_file, indent=4)
            json_file.write(',\n')  # Ensure each entry is on a new line and separated by a comma
        except json.JSONDecodeError:
            print("Failed to decode JSON response:", result)

result: 
    {
        "addresses": [
            "Alemany Blvd, San Francisco, CA 94112, USA"
        ]
    }
result: 
    {
        "addresses": []
    }
result: 
    {
        "addresses": []
    }
result: 
    {
        "addresses": []
    }
result: 
    {
        "addresses": []
    }
result: 
    {
        "addresses": [
            "564 Market St #225, San Francisco, CA 94104, USA"
        ]
    }
result: 
    {
        "addresses": []
    }
result: 
    {
        "addresses": []
    }
result: 
    {
        "addresses": [
            "1266 Harrison St, San Francisco, CA 94103, USA"
        ]
    }
result: 
    {
        "addresses": []
    }
result: 
    {
        "addresses": [
            "2128 Folsom St, San Francisco, CA 94110, USA"
        ]
    }
result: 
    {
        "addresses": []
    }
result: 
    {
        "addresses": []
    }
result: 
    {
        "addresses": [
            "1127 Kearny St, San Francisco, CA 94133, USA"
        ]
    }
result: 
    {
        "ad

In [78]:
#fix json

import json

# Function to fix the JSON format
def fix_json_format(file_path):
    with open(file_path, 'r') as file:
        content = file.read()
    
    # Fix the JSON format by ensuring it is a valid JSON array
    content = content.rstrip(',\n')  # Remove the trailing comma and newline
    fixed_content = f'[{content}]'
    
    # Write the fixed content to a new file
    with open('fixed_new_fixed_processed_results.json', 'w') as file:
        file.write(fixed_content)

    # Verify the fixed JSON
    with open('fixed_new_fixed_processed_results.json', 'r') as file:
        data = json.load(file)
        print(json.dumps(data, indent=4))
    return data

# Fix the JSON format of the existing file
data = fix_json_format('new_fixed_processed_results.json')

# Count how many objects have an address
address_count = 0

for entry in data:
    if "addresses" in entry["result"] and entry["result"]["addresses"]:
        address_count += 1

print(f"Number of objects with an address: {address_count}")

[
    {
        "query": "Jet Admin San Francisco",
        "result": {
            "addresses": [
                "Alemany Blvd, San Francisco, CA 94112, USA"
            ]
        }
    },
    {
        "query": "Legionfarm San Francisco",
        "result": {
            "addresses": []
        }
    },
    {
        "query": "Menten AI San Francisco",
        "result": {
            "addresses": []
        }
    },
    {
        "query": "Equator Therapeutics San Francisco",
        "result": {
            "addresses": []
        }
    },
    {
        "query": "Dapi San Francisco",
        "result": {
            "addresses": []
        }
    },
    {
        "query": "Prelay San Francisco",
        "result": {
            "addresses": [
                "564 Market St #225, San Francisco, CA 94104, USA"
            ]
        }
    },
    {
        "query": "Airbyte San Francisco",
        "result": {
            "addresses": []
        }
    },
    {
        "query": "Tambua Health

In [80]:
#number of objects with an address
import json

# Load the dataset
with open('fixed_new_fixed_processed_results.json', 'r') as json_file:
    data = json.load(json_file)

# Count how many objects have an address
address_count = 0

for entry in data:
    if "addresses" in entry["result"] and entry["result"]["addresses"]:
        address_count += 1

print(f"Number of objects with an address: {address_count}")

Number of objects with an address: 339


In [83]:
#something like "YC companies in San Francisco" is a good title and below that a information and star on github button

#create new dataset with address converted to lat and lon 

#open 'fixed_new_fixed_processed_results.json and take each address and convert it to lat lon and add it to new dataset together with query (only the fields which actually have an address also)
import json
import os
import requests
from dotenv import load_dotenv

# Load environment variables from .env file
load_dotenv()

# Google Maps Geocoding API endpoint
GEOCODING_API_URL = "https://maps.googleapis.com/maps/api/geocode/json"

# Retrieve API key from environment variables
API_KEY = os.getenv('GOOGLE_MAPS_API_KEY')

def geocode_address(address):
    params = {
        'address': address,
        'key': API_KEY
    }
    response = requests.get(GEOCODING_API_URL, params=params)
    if response.status_code == 200:
        data = response.json()
        if data['status'] == 'OK':
            location = data['results'][0]['geometry']['location']
            return location['lat'], location['lng']
    return None, None

# Load the fixed JSON data
with open('fixed_new_fixed_processed_results.json', 'r') as json_file:
    data = json.load(json_file)

# Open the new dataset file in append mode
with open('geocoded_results.json', 'a') as json_file:
    for entry in data:
        query = entry["query"]
        addresses = entry["result"].get("addresses", [])
        
        for address in addresses:
            lat, lon = geocode_address(address)
            if lat and lon:
                result = {
                    "query": query,
                    "address": address,
                    "latitude": lat,
                    "longitude": lon
                }
                json.dump(result, json_file, indent=4)
                json_file.write(',\n')  # Ensure each entry is on a new line and separated by a comma

print("Geocoding complete. Results saved to geocoded_results.json")

Geocoding complete. Results saved to geocoded_results.json


In [89]:
#load geocoding stuff and check that there are no duplicates
import json

# Load the geocoded JSON data
with open('geocoded_results.json', 'r') as json_file:
    data = json.load(json_file)

# Use a set to track unique queries or addresses
seen_queries = set()
duplicates = []

for entry in data:
    query = entry["query"]  # You can change this to entry["address"] if you want to check addresses instead
    if query in seen_queries:
        duplicates.append(query)
    else:
        seen_queries.add(query)

# Print duplicates
if duplicates:
    print("Duplicates found:", duplicates)
else:
    print("No duplicates found.")

No duplicates found.


In [90]:
# Load geocoding data and check for entries with more than one address
import json

# Load the geocoded JSON data
with open('geocoded_results.json', 'r') as json_file:
    data = json.load(json_file)

# Track entries with more than one address
multiple_addresses_entries = []

for entry in data:
    addresses = entry.get("addresses", [])
    if len(addresses) > 1:
        multiple_addresses_entries.append(entry)

# Print entries with more than one address
if multiple_addresses_entries:
    print("Entries with more than one address found:")
    for entry in multiple_addresses_entries:
        print(json.dumps(entry, indent=4))
else:
    print("No entries with more than one address found.")

No entries with more than one address found.


In [92]:
import json

# Path to the original file
input_file_path = 'company_data_updated.json'
# Path to the new file with corrected JSON
output_file_path = 'corrected_company_data.json'

try:
    # Read the original file
    with open(input_file_path, 'r') as file:
        # Read all lines in the file
        lines = file.readlines()
        # Remove newline characters and add a comma at the end of each line except the last one
        lines = [line.strip() + ',' if i < len(lines) - 1 else line.strip() for i, line in enumerate(lines)]
        # Join all lines and wrap them with square brackets to form a valid JSON array
        json_data = '[' + ''.join(lines) + ']'
        # Parse and reformat the JSON data
        data = json.loads(json_data)
    
    # Write the corrected JSON data to a new file
    with open(output_file_path, 'w') as file:
        json.dump(data, file, indent=4)
    
    print(f"Corrected JSON data has been saved to {output_file_path}")

except Exception as e:
    print(f"An error occurred: {e}")

Corrected JSON data has been saved to corrected_company_data.json


In [95]:
#next i want to create the final dataset which contains all the data from updated comp data and the data from geocoded_results

#next i want to iterate over the dataset geocoded_results and remove "San Francisco" from the query and than i want to find this query inside company_data_updated.json and than i want to take this row from company_data_updated.json and add the address from geocoded_results to it inside a new file
import json

# Load the geocoded JSON data
with open('geocoded_results.json', 'r') as geo_file:
    geocoded_data = json.load(geo_file)

# Load the company data
with open('corrected_company_data.json', 'r') as company_file:
    company_data = json.load(company_file)

# Create a dictionary for quick lookup of company data by query
company_dict = {entry["name"]: entry for entry in company_data}

# Prepare the new dataset
merged_data = []

for geo_entry in geocoded_data:
    # Remove "San Francisco" from the query
    query = geo_entry["query"].replace(" San Francisco", "")
    # Find the corresponding entry in company_data_updated.json
    if query in company_dict:
        company_entry = company_dict[query]
        # Merge the address information
        merged_entry = {
            **company_entry,
            "address": geo_entry["address"],
            "latitude": geo_entry["latitude"],
            "longitude": geo_entry["longitude"]
        }
        # Add the merged entry to the new dataset
        merged_data.append(merged_entry)

# Write the merged data to a new file
with open('merged_company_data.json', 'w') as output_file:
    json.dump(merged_data, output_file, indent=4)

print("Merging complete. Results saved to merged_company_data.json")

Merging complete. Results saved to merged_company_data.json


In [96]:
#load merged_company_data and count objects
import json

# Load the merged company data
with open('merged_company_data.json', 'r') as file:
    merged_data = json.load(file)

# Count the number of objects
num_objects = len(merged_data)

print(f"Number of objects in merged_company_data.json: {num_objects}")

Number of objects in merged_company_data.json: 339


In [97]:
#so now i can create the map with the merged data and display the companies on the map 
import json

def count_lines_in_notebook(notebook_path):
    with open(notebook_path, 'r', encoding='utf-8') as file:
        notebook = json.load(file)
    
    line_count = 0
    for cell in notebook['cells']:
        if cell['cell_type'] == 'code':
            line_count += len(cell['source'])
        elif cell['cell_type'] == 'markdown':
            line_count += len(cell['source'])
    return line_count

# Replace 'your_notebook.ipynb' with the path to your notebook file
notebook_path = 'google_maps.ipynb'
total_lines = count_lines_in_notebook(notebook_path)
print(f'Total number of lines in the notebook: {total_lines}')

Total number of lines in the notebook: 544
